In [1]:
import networkx as nx
import numpy as np
import pickle
import numpy as np
import os
import powerlaw
import seaborn as sns
import matplotlib.pyplot as plt

from scipy.stats import linregress
from scipy import optimize

Matplotlib settings for blury-less plotting in Jupyter NB:

In [2]:
%config InlineBackend.figure_format = 'svg'

Loads degrees and graphs:

In [3]:
%run 'create-final-graphs.ipynb'

Local clustering coefficient as a function of the node degree:

In [4]:
def get_cc_stats(graph):
    # get the largest connected component
    try:
        g = max(nx.strongly_connected_component_subgraphs(graph), key=len)
    except nx.NetworkXNotImplemented:
        g = max(nx.connected_component_subgraphs(graph), key=len)

    # convert it to an undireted graph
    g = g.to_undirected()

    # get nodes in the largest cc 
    nodes = nx.nodes(g)

    # compute inidivdual clustering coefficients
    indvd_cc = nx.algorithms.clustering(g, nodes=nodes)

    return pd.DataFrame(
        [(word, deg, indvd_cc[word]) for word, deg in list(g.degree(nodes))],
        columns=['word', 'k', 'c'])

Create an individiual dataframe for every graph with all nodes and their clustering coefficients:

In [5]:
df_cc = {}

graph_labels = graphs.keys()

for i, lab in enumerate(graph_labels):
    df = get_cc_stats(graphs[lab])
    df_cc[lab] = df

Scatter plots:

In [6]:
plt.figure(figsize=(16, 10))

# dictate order
graph_labels = ['USF_undirected', 'glove-cos', 'word2vec-cos', 'USF_directed',  
                'glove-cs-cos',  'glove-knn-cos',  'w2v-cs-cos', 'w2v-knn-cos']
nr_rows, nr_cols = 2, 4

for i, lab in enumerate(graph_labels):
    title = lab
    if 'cos' in title:
        title = lab[:lab.find('cos')-1]

    title = title.replace('_', ' ').replace('w2v', 'word2vec')
    
    ax = plt.subplot(nr_rows, nr_cols, i+1)
    df = df_cc[lab]
    mean_cc = df.groupby('k').mean()
    
    sns.regplot('k', 'c', data=df, fit_reg=False, scatter_kws={"marker": "x", "s": 1}, ax=ax) 
    sns.despine()
    
    nonzero_idx = mean_cc.c > 0
    ax.plot(mean_cc.index[nonzero_idx], mean_cc.c[nonzero_idx], color='r')
    
    res = linregress(np.log(mean_cc.index[nonzero_idx]), np.log(mean_cc.c[nonzero_idx]))
    print(lab, res.pvalue)
    
    regdat = r'$\gamma$=%.2f (r=%.2f)'%(-res.slope,res.rvalue)
    ax.annotate(regdat, xy=(35, .012))

    ax.set_title(title.replace('_', ' '))
    ax.set_ylim(10**-2,10**0+0.1)
    ax.set_xlim(10**0,10**3)
    ax.set_xscale('log')
    ax.set_yscale('log')
    if i < nr_cols:
        ax.xaxis.set_ticklabels([])
        ax.set_xlabel('')
    if i!=0 and i!=nr_cols:
        ax.yaxis.set_ticklabels([])
        ax.set_ylabel('')
plt.show()

USF_undirected 1.9302603893876344e-86
glove-cos 6.541018265396026e-05
word2vec-cos 1.6957074764502852e-09
USF_directed 1.1108026143063355e-86
glove-cs-cos 9.335058652680048e-27
glove-knn-cos 5.444926563573289e-43
w2v-cs-cos 1.3842455404153764e-09
w2v-knn-cos 5.4726966413716584e-21
